In [1]:
import json
import subprocess
from pprint import pprint
from pathlib import Path

In [2]:
# Basic Information
root = Path()
info_path = root / 'info'
data_pre = root / 'data' / 'data_pre_proc'
data_out = root / 'data' / 'data_proc'
data_out.mkdir(exist_ok=True)


In [3]:
channels = ['32', '37', '49', '54']

In [4]:
exp_dict_file = info_path / 'experiment_dict.json'
with open(exp_dict_file) as f:
   exp_dict = json.load(f)
f.close()
exp_dict

{'01': {'Experiment': 1, 'Type': ' Baseline', 'Activity': 'Eyes Open'},
 '02': {'Experiment': 2, 'Type': ' Baseline', 'Activity': 'Eyes Closed'},
 '03': {'Experiment': 3, 'Type': ' Real', 'Activity': 'Left Right'},
 '04': {'Experiment': 4, 'Type': ' Imaginary', 'Activity': 'Left Right'},
 '05': {'Experiment': 5, 'Type': ' Real', 'Activity': 'Top Down'},
 '06': {'Experiment': 6, 'Type': ' Imaginary', 'Activity': 'Top Down'},
 '07': {'Experiment': 7, 'Type': ' Real', 'Activity': 'Left Right'},
 '08': {'Experiment': 8, 'Type': ' Imaginary', 'Activity': 'Left Right'},
 '09': {'Experiment': 9, 'Type': ' Real', 'Activity': 'Top Down'},
 '10': {'Experiment': 10, 'Type': ' Imaginary', 'Activity': 'Top Down'},
 '11': {'Experiment': 11, 'Type': ' Real', 'Activity': 'Left Right'},
 '12': {'Experiment': 12, 'Type': ' Imaginary', 'Activity': 'Left Right'},
 '13': {'Experiment': 13, 'Type': ' Real', 'Activity': 'Top Down'},
 '14': {'Experiment': 14, 'Type': ' Imaginary', 'Activity': 'Top Down'}}

In [5]:
experiment_list = ['03', '04', '05', '06', '07','08', '09','10','11', '12', '13', '14']

In [6]:
# For every subject in the study
for subj_path in data_pre.glob('*/'):
    print(subj_path)
    # Get Subject code
    subj = subj_path.stem
    print('Subject-------> ', subj)
    # Make out folder for subject
    subj_folder_out = data_out / subj
    subj_folder_out.mkdir(exist_ok=True)
    # for every experiment with the subject
    for expe_num in experiment_list:
        print('experiment number ----> ', expe_num)
        expe_dir = exp_dict[expe_num]['Activity']
        expe_RI = exp_dict[expe_num]['Type']        
        # make output files
        base_path = data_pre / subj / "_".join([subj, expe_num])
        out_path = subj_folder_out / "_".join([subj, expe_num])
        # make output folder for experiment
        out_path.mkdir(exist_ok=True)
        print('>>> Starting DMCx2 ...')
        # for each channel as y variable
        for j in range(len(channels)):
            cha = channels[j:] + channels[:j]
            print('Channels list', cha)
            p = subprocess.Popen(['dccamult_4ts.exe'], stdin=subprocess.PIPE, stdout=subprocess.PIPE, text=True)
            # Inputs
            for i in range(4):
                file_aux = base_path / ("_".join([subj , expe_num , cha[i]]) + '.txt')
                print(i ,': ', file_aux)
                p.stdin.write( str(file_aux) + '\n')
            # Outputs
            str_aux ="_"
            result1 = out_path / (subj + '_' + expe_num + '_DMCX2_' + str_aux.join(cha)+ '.txt')
            result2 =  out_path / (subj + '_' + expe_num + '_PDCCA_' + str_aux.join(cha)+ '.txt')
            print('Output_files:\n\t\t{}\n\t\t{}'.format(result1, result2))
            p.stdin.write(str(result1) + '\n')
            p.stdin.write(str(result2) + '\n')
            out, err = p.communicate()
            print('shell out: ')
            pprint(out)
            pprint(err)
            print(p.poll())
print('end')

data\data_pre_proc\S001
Subject------->  S001
experiment number ---->  03
>>> Starting DMCx2 ...
Channels list ['32', '37', '49', '54']
0 :  data\data_pre_proc\S001\S001_03\S001_03_32.txt
1 :  data\data_pre_proc\S001\S001_03\S001_03_37.txt
2 :  data\data_pre_proc\S001\S001_03\S001_03_49.txt
3 :  data\data_pre_proc\S001\S001_03\S001_03_54.txt
Output_files:
		data\data_proc\S001\S001_03\S001_03_DMCX2_32_37_49_54.txt
		data\data_proc\S001\S001_03\S001_03_PDCCA_32_37_49_54.txt
shell out: 
('Enter the first time series to be read: (dependent variable, y)\n'
 'Enter the second time series to be read: (independent variable, x1)\n'
 '(....with the same length N):\n'
 'Enter the third time series to be read: (independent variable, x2)\n'
 '(....with the same length N):\n'
 'Enter the fourth time series to be read: (independent variable, x3)\n'
 '(....with the same length N):\n'
 'Enter the name for DMCx^2: {y;(x1,x2,x3)}?\n'
 'Enter the name for the cross-correlation coefficient combinations?\n

## Fix separator

In [7]:
def replace_in_file(file_path, str1, str2):
    #read input file
    f_in = open(file_path, "rt")
    #read file contents to string
    data = f_in.read()
    #replace all occurrences of the required string
    data = data.replace(str1, str2)
    #close the input file
    f_in.close()
    #open the same file in write mode
    f_out = open(file_path, "wt")
    #overrite the file with the resulting data
    f_out.write(data)
    #close the file
    f_out.close()

In [8]:
files_dmc = data_out.glob('**/**/*DMCX2*.txt')
files_PDCCA = data_out.glob('**/**/*PDCCA*.txt')
for file in files_PDCCA:
    print(file)
    replace_in_file(file, ',', '')
    

data\data_proc\S001\S001_03\S001_03_PDCCA_32_37_49_54.txt
data\data_proc\S001\S001_03\S001_03_PDCCA_37_49_54_32.txt
data\data_proc\S001\S001_03\S001_03_PDCCA_49_54_32_37.txt
data\data_proc\S001\S001_03\S001_03_PDCCA_54_32_37_49.txt
data\data_proc\S001\S001_04\S001_04_PDCCA_32_37_49_54.txt
data\data_proc\S001\S001_04\S001_04_PDCCA_37_49_54_32.txt
data\data_proc\S001\S001_04\S001_04_PDCCA_49_54_32_37.txt
data\data_proc\S001\S001_04\S001_04_PDCCA_54_32_37_49.txt
data\data_proc\S001\S001_05\S001_05_PDCCA_32_37_49_54.txt
data\data_proc\S001\S001_05\S001_05_PDCCA_37_49_54_32.txt
data\data_proc\S001\S001_05\S001_05_PDCCA_49_54_32_37.txt
data\data_proc\S001\S001_05\S001_05_PDCCA_54_32_37_49.txt
data\data_proc\S001\S001_06\S001_06_PDCCA_32_37_49_54.txt
data\data_proc\S001\S001_06\S001_06_PDCCA_37_49_54_32.txt
data\data_proc\S001\S001_06\S001_06_PDCCA_49_54_32_37.txt
data\data_proc\S001\S001_06\S001_06_PDCCA_54_32_37_49.txt
data\data_proc\S001\S001_07\S001_07_PDCCA_32_37_49_54.txt
data\data_proc

In [9]:
import pandas as pd
files_PDCCA = data_out.glob('**/**/*PDCCA*.txt')
list_files = list(files_PDCCA)
df = pd.read_csv(list_files[0], sep=' ')
df.head()

n     rho12     rho13     rho14     rho23     rho24     rho34
0   4  0.862423  0.600387  0.504383  0.471001  0.465070  0.727005
1   5  0.870990  0.602111  0.507064  0.472922  0.467391  0.723646
2   7  0.884340  0.612943  0.521263  0.485213  0.481024  0.730769
3   9  0.892737  0.624064  0.537765  0.495411  0.494645  0.744271
4  11  0.897794  0.632980  0.553454  0.501464  0.506221  0.758850